# File operations and command line
We will learn how read and write files from Python and how to write a Python program and run it from the command line. 

## Reading and writing files

Python handles files through file objects. 

The `open(filename[, mode])` function opens a file and returns a file handle object (or raise an error).
The `mode` can be `'r'` (read), `'w'` (write), `'r+'` (both), `'a'` (append), `'a+'` (append+read), or in case of binary files
`'rb'`, `'wb'`, `'r+b'`, `'ab'`, `'a+b'`.: `'rb'`, `'wb'`, `'r+b'`.

In [ ]:
f = open('E0.csv')  # open for reading, return a file object
print(f)
print(type(f))

The file object is not so useful on its own.
This file contains the English Premier League statistics from the season of 2015/16.
The `read()` method reads the whole file to a string. We print out the first 100 chars only:

In [ ]:
f = open('E0.csv')
content = f.read()
print(content[:100])

Note: opening a text file for reading we may use `open('E0.csv', 'r')` but reading is the default, so you may drop `'r'`.

Read in the first and second lines with the `readline()` method. Every call of this method return the **next line** of the file.

In [ ]:
f = open('E0.csv')
first_line = f.readline()
print(first_line)
second_line = f.readline()
print(second_line)

The file object is _iterable_ row-wise.

Mind the newline character at the end of each line.

In [ ]:
f = open('E0.csv')
lst = []
for line in f:
    lst.append(line)
print(lst[:4])

The list `lst` now contains the rows of the file. You can split the lines into cells with `.split(",")` but later we will show an other method.

## Writing a file
Let's say that you care only about the results of the team 'Liverpool'.
Write the appropriate data into a file named `'Liverpool.csv'`.

For writing we open with `open(filename, 'w')`, **but if you do so, don't forget to close it!**

In [ ]:
f = open('Liverpool.csv', 'w')
f.write('YNWA')  # You'll Never Walk Alone
f.close()

Or you may use an equivalent but safer practice with the command `with`, as it calls `close()` *automaticly* when it steps out from the scope of it.

In [ ]:
with open('Liverpool.csv', 'w') as f:
    f.write('When you walk through a storm\n')
print("OK, the file is closed now.")

Let us add a new line to the closed file:

In [ ]:
with open('Liverpool.csv', 'a') as f:
    f.write('Hold your head up high\n')

Let's read the results row-by-row and choose the rows containing the word 'Liverpool', save those line in 'Liverpool.csv'.
The header of the file will be the same!

In [ ]:
f = open('E0.csv')
lst = [f.readline()]   # this is the header

for line in f:
    if 'Liverpool' in line:
        lst.append(line)

with open('Liverpool.csv', 'w') as f:
    for l in lst:
        f.write(l)

### Reading and writing binary files
Write some numbers into bytes, and read them back!

In [ ]:
with open("binfile.bin", "wb") as f:
    numbs = [1, 2, 4, 8, 16, 32, 31]
    arr = bytearray(numbs)
    f.write(arr)

In [ ]:
with open("binfile.bin", "rb") as f:
    numbs = list(f.read())
    print(numbs)

## Handling `csv`  files in Python
The meaning of `.csv` file extenstion is **comma separated values** (see [Wikipedia](https://en.wikipedia.org/wiki/Comma-separated_values)).
Each line of these type of files is a data record. Each record consists of one or more fields, separated by commas. Comma is the default separator, but one may use other character to separate. The spreadsheet programs (like Excel, libreoffice) can load and save the files in this format.

Python can handle this format with the `csv` module (see [Python documentation](https://docs.python.org/3/library/csv.html)).

In [ ]:
import csv

l = []
with open('E0.csv', 'r') as csvfile:
    reader = csv.reader(csvfile)  # , delimiter=',', quotechar='"')
    for row in reader:
        l.append(row)

print(l[0])
print(l[19])

This result differs from the previous one: `csv.reader()` makes a list from the lines. In comment we gave two optional values what we may use: with the option `delimiter` one may change the default separator comma to an other character, and with `quotechar` one may define which character to use to delimit strings. This is useful when there are numbers and strings mixed in the file.

### Reading csv format into a dictionary
If you look the data closely, you can see that a dictionary would be even better.
It's better to refer the cells by name and not by index.

This format uses the first line (header) as dictionary keys. `DictReader()` function of the `csv` modul makes this:

In [ ]:
import csv

l = []
with open('E0.csv') as csvfile:
    reader = csv.DictReader(csvfile)
    for row in reader:
        l.append(row)

print(l[0])

The result is not what we hoped. This is not an ordinary dictionary, but something new. This is a so called **ordered dictionary**. An `OrderedDict` is a dictionary subclass that remembers the order in which its contents are added. Otherwise we may use exactly the same methods. To convert it to ordinary dictionary use the `dict` function:

In [ ]:
print(dict(l[0]))

To make an ordered dictionary we have to import the `collections` modul (`csv` do this otherwise). The next example show the difference between `dict` and `OrderedDict` dictionaries:

In [ ]:
import collections

d1 = {}
d1['x'] = 'X'
d1['y'] = 'Y'

d2 = {}
d2['y'] = 'Y'
d2['x'] = 'X'

print(d1 == d2)

d1 = collections.OrderedDict()
d1['x'] = 'X'
d1['y'] = 'Y'

d2 = collections.OrderedDict()
d2['y'] = 'Y'
d2['x'] = 'X'

print(d1 == d2)

Let us go back to our file and store the data of Liverpool matches only. We will write the 'Date', 'HomeTeam', 'AwayTeam', 'FTHG'(Full Time Home Goals), 'FTAG' (Full Time Away Goals), 'FTR' (Full Time Result) values into a file!
We will use `csv.DictWriter` to write the data, the `writeheader()` method to write the header first,
then the `writerows()` method to write the actual data.

The `fieldnames` parameter tells which fields (columns in the table) to use.
The `extrasaction='ignore'` ignores the other fields.

In [ ]:
import csv

l = []
with open('E0.csv') as csvfile:
    reader = csv.DictReader(csvfile)
    for x in reader:
        if x['HomeTeam'] == 'Liverpool' or x['AwayTeam'] == 'Liverpool':
            l.append(x)

print(dict(l[0]), dict(l[1]))

with open('Liverpool.csv', 'w') as output:
    fields = ['Date', 'HomeTeam', 'AwayTeam', 'FTHG', 'FTAG', 'FTR']
    writer = csv.DictWriter(output, fieldnames=fields, extrasaction='ignore')
    writer.writeheader()
    writer.writerows(l)

## Handling `json` format in Python

JSON (JavaScript Object Notation) is a lightweight language independent data-interchange format. The key structures of it are the list and dictionary, and the notation of them is the same as in Python: lists are marked with a comma separated list in brackets `[ ]`, the dict contains the usual `key:value` pairs in curly brackets `{ }`.

This is an example, you may copy it into a file:

    {
        "Liverpool" : {
            "Players": [
                "Steven Gerrard",
                "Bill Shankly"
            ],
            "Results" : [
                {
                    "HomeTeam":"Liverpool",
                    "AwayTeam":"Tottenham",
                    "HTG":1,
                    "ATG":1
                },
                {
                    "HomeTeam":"West Ham",
                    "AwayTeam":"Liverpool",
                    "HTG":2,
                    "ATG":0
                }
            ],
            "Points":1,
            "Goals Scored":1,
            "Goals Condceded":3
        }
    }

Python can hanle this format with the `json` module.
After reading the file, the `data` is saved in Python objects.

In [ ]:
import json

with open('Liverpool.json') as data_file:    
    data = json.load(data_file)

print(data, "\n")
print(data['Liverpool']['Players'])

Now let's write a json file! To look better you may use the `sort_keys`, `indent` and `separators` parameters.
The `json.dumps(obj)` returns a string which encodes an object (`obj`) in a json format.
We write that into a file and that's all.

In [ ]:
import json

with open('Liverpool.json') as data_file:    
    data = json.load(data_file)

with open('Liverpool_matches.json', 'w') as f:
    f.write(json.dumps(data['Liverpool']['Results'], 
            sort_keys=True, indent=4, separators=(',', ': ')))

There are sevaral ways to handle json format:
* `json.dumps(obj)`: encodes `obj` to a JSON formatted string (**dump s**tring)
* `json.dump(JSON_formatted_string, file)`: writes into a file
* `json.loads(JSON_formatted_string)`: converts a JSON formatted  string into a python object (**load s**tring)
* `json.load(file)`: reads the content of `file` to a python object (it can be a complex python data)

More details in [python docs](https://docs.python.org/3/library/json.html).

## Command line arguments

We will run python codes as standalone programs!

### The `sys` module

Write a python code and save it with the `.py` extension.
Your OS can recongise it as a python program or you can run with an interpreter.

You can communicate with your program  via `input()` function or with **command line arguments**.
Our very first program will write out the number of command line arguments and the list of them. 
The first element in this list is the name of the program file. The others are optional. 
To do this we have to `import sys` first. The list `sys.argv` will store these parameters. Important note: this is a **list of strings**! Even the numbers are stored as strings, so using them as numbers, we have to convert them.

Save the followings into a file named **cli.py** and run from command line.

~~~ python
import sys

print('Number of arguments:', len(sys.argv))
print('List of arguments:  ', sys.argv)
~~~

In [ ]:
!python3 cli.py arg1 arg2

The `!` tells the notebook to run in command line, not here as a python code.

You can use the values in `sys.argv` and we call them *positional parameters* since you can refer to them by their place in the list `sys.argv`.

**Exercise:** calculate the power of a number.
Write a python program which have two command line arguments: base and exponent.

If the numbers are integers then calculate as integers, otherwise calculate with floats.

Save the followings into a file named **power.py**.

~~~ python
import sys

def is_intstring(s):
    try:
        int(s)
        return True
    except ValueError:
        return False

a = []

for i in range(1,3):
    if is_intstring(sys.argv[i]):
        a.append(int(sys.argv[i]))
    else:
        a.append(float(sys.argv[i]))

print(a[0] ** a[1])
~~~

This is how to run it:

In [ ]:
!python3 power.py 4.2 3

!python3 power.py 2 100

In Linux, if the first line of the Python file is 
```Python
#!/usr/bin/python3
```
and the file is executable (if not, use ```chmod +x filename```), then you may run the code without the ```python3``` command:

In [ ]:
!power.py 2 1000